## StockOut duration generation
## Selecion of X

In [2]:
import pickle
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from datetime import datetime, date
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.dates as md
import seaborn as sns
import datetime
from datetime import datetime, timedelta, time
from tqdm import tqdm
import statsmodels.formula.api as sm
from statsmodels.iolib.summary2 import summary_col

import warnings
warnings.filterwarnings("ignore")

from tqdm import tqdm


pd.set_option('display.max_rows', 500)
pd.options.mode.chained_assignment = None 
# !dir 00_pickle_to_csv

- Loading Sales data

In [3]:
# Load data from the file
with open('C:/Users/gaura/BSE/MS THESIS/1_Glovo Data from Alberto/sales.pkl', 'rb') as f:
    sales_rawdata = pickle.load(f)

df_sales = pd.DataFrame(sales_rawdata)

In [4]:
df_sales

order_id store_id  order_date product_id customer_id  \
0         42160        0  2022-12-31        742       15213   
1         17111        0  2022-12-31       3834       19259   
2         17111        0  2022-12-31        779       19259   
3         17111        0  2022-12-31        475       19259   
4         17111        0  2022-12-31       4236       19259   
...         ...      ...         ...        ...         ...   
832603     1997        0  2023-01-28       1307       22736   
832604     1997        0  2023-01-28       2314       22736   
832605    32690        0  2023-01-28       3069       14236   
832606    32690        0  2023-01-28       3208       14236   
832607    32690        0  2023-01-28       1588       14236   

                                   product_name  sold_quantity  \
0                   Listerine blanqueante 500ml            2.0   
1                              Agua Bezoya 1.5L            2.0   
2       Carbonell Aceite de Oliva Suave 0.4º 1L            1.0   
3                  Zumo de naranja natural 0.5L            1.0   
4             Evax Compresa Cottonlike Alas 16u            1.0   
...                                         ...            ...   
832603              Papel higiénico Scottex 16u            1.0   
832604               Coca-Cola Light Botella 2L            6.0   
832605               Monster Cookie XXL de Oreo            1.0   
832606            Monster Cookie XXL de Nutella            1.0   
832607             Monster Cookie XXL de Kinder            1.0   

                  order_datetime  
0      2022-12-31 17:44:04+00:00  
1      2022-12-31 08:38:14+00:00  
2      2022-12-31 08:38:14+00:00  
3      2022-12-31 08:38:14+00:00  
4      2022-12-31 08:38:14+00:00  
...                          ...  
832603 2023-01-28 15:07:32+00:00  
832604 2023-01-28 15:07:32+00:00  
832605 2023-01-28 20:00:42+00:00  
832606 2023-01-28 20:00:42+00:00  
832607 2023-01-28 20:00:42+00:00  

[832608 rows x 8 columns]

- Loading Availability data

In [10]:
# Load data from the file
with open('C:/Users/gaura/BSE/MS THESIS/1_Glovo Data from Alberto/availability.pkl', 'rb') as f:
    availability_rawdata = pickle.load(f)

df_availability = pd.DataFrame(availability_rawdata)

In [11]:
# Changing a column name
df_availability.rename(columns={'available_as_end_of_day': 'available_at_end_of_day'}, inplace=True)

- Processing the Availability data
    1. creating the end_of_day timestamp as 23:59:59 that is 1 sec before midnight
    2. availbility status at_end_of_day is known
    3. creating the start_of_day timestamp as 00:00:01 that is 1 sec into start of day
    4. availbility status at_start_of_day has to be infered or defined

In [12]:
# Format the datetime values
import pandas as pd
from datetime import datetime, timedelta

# Convert order_date column to datetime
df_availability['order_date'] = pd.to_datetime(df_availability['order_date'])

# Set the time to one second before midnight
df_availability['datetime_at_end_of_day'] = df_availability['order_date'].apply(lambda x: x.replace(hour=23, minute=59, second=59) - timedelta(seconds=1))

# Format datetime_at_end_of_day column to match datetime_at_start_of_day format
df_availability['datetime_at_end_of_day'] = df_availability['datetime_at_end_of_day'].dt.strftime('%Y-%m-%d %H:%M:%S+00:00')

# Set datetime_at_start_of_day column with the desired format
df_availability['datetime_at_start_of_day'] = df_availability['order_date'].apply(lambda x: x.replace(hour=0, minute=0, second=1).strftime('%Y-%m-%d %H:%M:%S+00:00'))

# Verify the updated DataFrame
#df_availability.head()

- Creating a sorted_sales dataframe

In [13]:
sorted_sales = df_sales.sort_values(by=['product_id', 'order_date', 'order_datetime']).reset_index(drop=True)


In [14]:
sorted_sales

order_id store_id  order_date product_id customer_id  \
0         22580        0  2022-01-01          0       31814   
1         34592        0  2022-01-07          0        9628   
2         96719        0  2022-01-07          0       32180   
3        116469        0  2022-01-08          0       20226   
4         44020        0  2022-01-08          0       27749   
...         ...      ...         ...        ...         ...   
832603   134833        0  2023-03-17        999        4477   
832604     8269        0  2023-03-17        999        3955   
832605   137423        0  2023-03-21        999       32165   
832606    23847        0  2023-03-21        999        5401   
832607    60452        0  2023-03-30        999        4477   

                                   product_name  sold_quantity  \
0       Bimbo Pan de Molde Estilo Artesano 550g            1.0   
1       Bimbo Pan de Molde Estilo Artesano 550g            1.0   
2       Bimbo Pan de Molde Estilo Artesano 550g            1.0   
3       Bimbo Pan de Molde Estilo Artesano 550g            1.0   
4       Bimbo Pan de Molde Estilo Artesano 550g            1.0   
...                                         ...            ...   
832603                 Realfooding Madalenas 2u            1.0   
832604                 Realfooding Madalenas 2u            1.0   
832605                 Realfooding Madalenas 2u            1.0   
832606                 Realfooding Madalenas 2u            1.0   
832607                 Realfooding Madalenas 2u            1.0   

                  order_datetime  
0      2022-01-01 09:30:44+00:00  
1      2022-01-07 21:04:18+00:00  
2      2022-01-07 21:23:32+00:00  
3      2022-01-08 09:51:52+00:00  
4      2022-01-08 11:46:27+00:00  
...                          ...  
832603 2023-03-17 06:48:14+00:00  
832604 2023-03-17 08:15:58+00:00  
832605 2023-03-21 00:08:02+00:00  
832606 2023-03-21 18:47:18+00:00  
832607 2023-03-30 12:32:59+00:00  

[832608 rows x 8 columns]

- Adding first_order_timestamp & last_order_timestamp to the sorted_sales dataframe

In [15]:
# Convert 'order_datetime' column to datetime data type
sorted_sales['order_datetime'] = pd.to_datetime(sorted_sales['order_datetime'])

# Calculate first and last order timestamps for each product ID and order date
first_order_timestamp = sorted_sales.groupby(['product_id', 'order_date'])['order_datetime'].transform('min')
last_order_timestamp = sorted_sales.groupby(['product_id', 'order_date'])['order_datetime'].transform('max')

# Add the new columns to the dataframe
sorted_sales['first_order_timestamp'] = first_order_timestamp
sorted_sales['last_order_timestamp'] = last_order_timestamp

In [16]:
sorted_sales

order_id store_id  order_date product_id customer_id  \
0         22580        0  2022-01-01          0       31814   
1         34592        0  2022-01-07          0        9628   
2         96719        0  2022-01-07          0       32180   
3        116469        0  2022-01-08          0       20226   
4         44020        0  2022-01-08          0       27749   
...         ...      ...         ...        ...         ...   
832603   134833        0  2023-03-17        999        4477   
832604     8269        0  2023-03-17        999        3955   
832605   137423        0  2023-03-21        999       32165   
832606    23847        0  2023-03-21        999        5401   
832607    60452        0  2023-03-30        999        4477   

                                   product_name  sold_quantity  \
0       Bimbo Pan de Molde Estilo Artesano 550g            1.0   
1       Bimbo Pan de Molde Estilo Artesano 550g            1.0   
2       Bimbo Pan de Molde Estilo Artesano 550g            1.0   
3       Bimbo Pan de Molde Estilo Artesano 550g            1.0   
4       Bimbo Pan de Molde Estilo Artesano 550g            1.0   
...                                         ...            ...   
832603                 Realfooding Madalenas 2u            1.0   
832604                 Realfooding Madalenas 2u            1.0   
832605                 Realfooding Madalenas 2u            1.0   
832606                 Realfooding Madalenas 2u            1.0   
832607                 Realfooding Madalenas 2u            1.0   

                  order_datetime     first_order_timestamp  \
0      2022-01-01 09:30:44+00:00 2022-01-01 09:30:44+00:00   
1      2022-01-07 21:04:18+00:00 2022-01-07 21:04:18+00:00   
2      2022-01-07 21:23:32+00:00 2022-01-07 21:04:18+00:00   
3      2022-01-08 09:51:52+00:00 2022-01-08 09:51:52+00:00   
4      2022-01-08 11:46:27+00:00 2022-01-08 09:51:52+00:00   
...                          ...                       ...   
832603 2023-03-17 06:48:14+00:00 2023-03-17 06:48:14+00:00   
832604 2023-03-17 08:15:58+00:00 2023-03-17 06:48:14+00:00   
832605 2023-03-21 00:08:02+00:00 2023-03-21 00:08:02+00:00   
832606 2023-03-21 18:47:18+00:00 2023-03-21 00:08:02+00:00   
832607 2023-03-30 12:32:59+00:00 2023-03-30 12:32:59+00:00   

            last_order_timestamp  
0      2022-01-01 09:30:44+00:00  
1      2022-01-07 21:23:32+00:00  
2      2022-01-07 21:23:32+00:00  
3      2022-01-08 17:17:02+00:00  
4      2022-01-08 17:17:02+00:00  
...                          ...  
832603 2023-03-17 08:15:58+00:00  
832604 2023-03-17 08:15:58+00:00  
832605 2023-03-21 18:47:18+00:00  
832606 2023-03-21 18:47:18+00:00  
832607 2023-03-30 12:32:59+00:00  

[832608 rows x 10 columns]

- Creating the modified_sorted_sales DataFrame that includes only the specified columns from the sorted_sales DataFrame to remove the duplicacy of order_date

In [17]:
modified_sorted_sales = sorted_sales[['order_date', 'product_id', 'product_name', 'first_order_timestamp', 'last_order_timestamp']].copy()
#modified_sorted_sales

In [18]:
# without the order_id column there were many duplicates which we dont need, so we drop the duplicates
modified_sorted_sales = modified_sorted_sales.drop_duplicates()
#modified_sorted_sales

- Creating a sorted_availability dataframe

In [19]:
sorted_availability = df_availability.sort_values(by=['product_id', 'order_date']).reset_index(drop=True)
#sorted_availability.info()

- Creating a "merged_sorted_availability" dataframe that adds first_order and last_order to sorted_availability dataframe

In [20]:
# Convert 'product_id' column to a common data type (e.g., str or int)
sorted_availability['product_id'] = sorted_availability['product_id'].astype(str)
modified_sorted_sales['product_id'] = modified_sorted_sales['product_id'].astype(str)

# Convert 'order_date' column to datetime data type
sorted_availability['order_date'] = pd.to_datetime(sorted_availability['order_date'])
modified_sorted_sales['order_date'] = pd.to_datetime(modified_sorted_sales['order_date'])

# Merge sorted_sales with sorted_availability on 'product_id' and 'order_date'
merged_sorted_availability = sorted_availability.merge(modified_sorted_sales[['product_id', 'order_date', 'first_order_timestamp', 'last_order_timestamp']], on=['product_id', 'order_date'], how='left')

- Adding a column "available_at_start_of_day" to the dataframe "merged_sorted_availability" and filling in values according to following rule:
    
    1.For rows where order_date = 2022-01-01 (first date of the dataset) we initialize the values as:
        (i)False where 'available_at_end_of_day'] == False & 'first_order_timestamp'].isnull()
        (ii)True otherwise
        
    2.For all other rows we initially leave values as Nan, later we use fillna() to fill in these values equal to the value of available_at_end_of_day of the previous day

In [21]:
# Check if order_date is equal to 2022-01-01 and apply the rule
merged_sorted_availability['available_at_start_of_day'] = np.where(
    merged_sorted_availability['order_date'] == '2022-01-01',
    np.where(
        (merged_sorted_availability['available_at_end_of_day'] == False) & (merged_sorted_availability['first_order_timestamp'].isnull()),
        False,
        True
    ),
    np.nan
)

merged_sorted_availability.head(100)

# Fill NaN values with previous available_at_end_of_day value
merged_sorted_availability['available_at_start_of_day'] = merged_sorted_availability['available_at_start_of_day'].fillna(
    merged_sorted_availability['available_at_end_of_day'].shift()
)


# Replace 1.0 with True and 0.0 with False
merged_sorted_availability['available_at_start_of_day'] = merged_sorted_availability['available_at_start_of_day'].map({1.0: True, 0.0: False})

- Rearranging the column order of the dataframe "merged_sorted_availability"

In [22]:
# Rearranging the order of the columns

column_order = [
    'store_id',
    'product_id',
    'order_date',
    'datetime_at_start_of_day',
    'available_at_start_of_day',
    'first_order_timestamp',
    'last_order_timestamp',
    'datetime_at_end_of_day',
    'available_at_end_of_day'
]

merged_sorted_availability = merged_sorted_availability.reindex(columns=column_order)


In [23]:
# Convert datetime_at_start_of_day and datetime_at_end_of_day columns to datetime64[ns, UTC]
merged_sorted_availability['datetime_at_start_of_day'] = pd.to_datetime(merged_sorted_availability['datetime_at_start_of_day'], utc=True)
merged_sorted_availability['datetime_at_end_of_day'] = pd.to_datetime(merged_sorted_availability['datetime_at_end_of_day'], utc=True)

In [24]:
# to avoid having a none value of the stockout_end for products which do not come back in stock at all
# we set the value of available_at_end_of_day as True for all product ids for order_date 2023-03-31 

merged_sorted_availability.loc[merged_sorted_availability['order_date'] == '2023-03-31', 'available_at_end_of_day'] = True



---

---

- # EDA to come up with rules for start+of_stockout & end_of_stockout 

In [25]:
# Investigating the stock availability status transitions 

# Filter the rows based on conditions
filtered_rows_FF_Na = merged_sorted_availability[
    ((merged_sorted_availability['available_at_start_of_day'] == False) &
    (merged_sorted_availability['available_at_end_of_day'] == False) &
    (merged_sorted_availability['first_order_timestamp'].isna()))
]

filtered_rows_FF_NotNa = merged_sorted_availability[
    ((merged_sorted_availability['available_at_start_of_day'] == False) &
    (merged_sorted_availability['available_at_end_of_day'] == False) &
    (~merged_sorted_availability['first_order_timestamp'].isna()))
]
 
filtered_rows_FT_Na = merged_sorted_availability[
    ((merged_sorted_availability['available_at_start_of_day'] == False) &
    (merged_sorted_availability['available_at_end_of_day'] == True) &
    (merged_sorted_availability['first_order_timestamp'].isna()))
]

filtered_rows_FT_NotNa = merged_sorted_availability[
    ((merged_sorted_availability['available_at_start_of_day'] == False) &
    (merged_sorted_availability['available_at_end_of_day'] == True) &
    (~merged_sorted_availability['first_order_timestamp'].isna()))
]

filtered_rows_TF_Na = merged_sorted_availability[
    ((merged_sorted_availability['available_at_start_of_day'] == True) &
    (merged_sorted_availability['available_at_end_of_day'] == False) &
    (merged_sorted_availability['first_order_timestamp'].isna()))
]

filtered_rows_TF_NotNa = merged_sorted_availability[
    ((merged_sorted_availability['available_at_start_of_day'] == True) &
    (merged_sorted_availability['available_at_end_of_day'] == False) &
    (~merged_sorted_availability['first_order_timestamp'].isna()))
]

filtered_rows_TT_Na = merged_sorted_availability[
    ((merged_sorted_availability['available_at_start_of_day'] == True) &
    (merged_sorted_availability['available_at_end_of_day'] == True) &
    (merged_sorted_availability['first_order_timestamp'].isna()))
]

filtered_rows_TT_NotNa = merged_sorted_availability[
    ((merged_sorted_availability['available_at_start_of_day'] == True) &
    (merged_sorted_availability['available_at_end_of_day'] == True) &
    (~merged_sorted_availability['first_order_timestamp'].isna()))
]

# Print the lengths of the filtered rows
print("filtered_rows_FF_Na:   ", len(filtered_rows_FF_Na))
print("filtered_rows_FF_NotNa:", len(filtered_rows_FF_NotNa))
print("filtered_rows_FT_Na:   ", len(filtered_rows_FT_Na))
print("filtered_rows_FT_NotNa:", len(filtered_rows_FT_NotNa))
print("filtered_rows_TF_Na:   ", len(filtered_rows_TF_Na))
print("filtered_rows_TF_NotNa:", len(filtered_rows_TF_NotNa))
print("filtered_rows_TT_Na:   ", len(filtered_rows_TT_Na))
print("filtered_rows_TT_NotNa:", len(filtered_rows_TT_NotNa))

# Calculate the total of all values
total = len(filtered_rows_FF_Na) + len(filtered_rows_FF_NotNa) + len(filtered_rows_FT_Na) + len(filtered_rows_FT_NotNa) + len(filtered_rows_TF_Na) + len(filtered_rows_TF_NotNa) + len(filtered_rows_TT_Na) + len(filtered_rows_TT_NotNa)
print("Total:", total)

filtered_rows_FF_Na:    797673
filtered_rows_FF_NotNa: 10480
filtered_rows_FT_Na:    8671
filtered_rows_FT_NotNa: 4816
filtered_rows_TF_Na:    1935
filtered_rows_TF_NotNa: 9550
filtered_rows_TT_Na:    784237
filtered_rows_TT_NotNa: 366438
Total: 1983800


- Investigating the doubtful transition FF_notNa

In [26]:

filtered_rows_FF_NotNa = merged_sorted_availability[
    ((merged_sorted_availability['available_at_start_of_day'] == False) &
    (merged_sorted_availability['available_at_end_of_day'] == False) &
    (~merged_sorted_availability['first_order_timestamp'].isna()))
]

filtered_rows_FF_NotNa


store_id product_id order_date  datetime_at_start_of_day  \
248             0          0 2022-09-06 2022-09-06 00:00:01+00:00   
3555            0          7 2023-01-06 2023-01-06 00:00:01+00:00   
4699            0         10 2022-05-30 2022-05-30 00:00:01+00:00   
15928           0         35 2022-01-04 2022-01-04 00:00:01+00:00   
15929           0         35 2022-01-05 2022-01-05 00:00:01+00:00   
...           ...        ...        ...                       ...   
1977538         0       4349 2022-04-19 2022-04-19 00:00:01+00:00   
1977539         0       4349 2022-04-20 2022-04-20 00:00:01+00:00   
1977544         0       4349 2022-04-25 2022-04-25 00:00:01+00:00   
1977546         0       4349 2022-04-27 2022-04-27 00:00:01+00:00   
1980775         0       4356 2022-06-10 2022-06-10 00:00:01+00:00   

         available_at_start_of_day     first_order_timestamp  \
248                          False 2022-09-06 16:16:34+00:00   
3555                         False 2023-01-06 06:01:32+00:00   
4699                         False 2022-05-30 19:32:53+00:00   
15928                        False 2022-01-04 21:30:12+00:00   
15929                        False 2022-01-05 11:31:16+00:00   
...                            ...                       ...   
1977538                      False 2022-04-19 17:43:43+00:00   
1977539                      False 2022-04-20 18:37:57+00:00   
1977544                      False 2022-04-25 18:38:20+00:00   
1977546                      False 2022-04-27 20:28:51+00:00   
1980775                      False 2022-06-10 12:54:44+00:00   

             last_order_timestamp    datetime_at_end_of_day  \
248     2022-09-06 16:16:34+00:00 2022-09-06 23:59:58+00:00   
3555    2023-01-06 06:01:32+00:00 2023-01-06 23:59:58+00:00   
4699    2022-05-30 19:32:53+00:00 2022-05-30 23:59:58+00:00   
15928   2022-01-04 21:30:12+00:00 2022-01-04 23:59:58+00:00   
15929   2022-01-05 11:31:16+00:00 2022-01-05 23:59:58+00:00   
...                           ...                       ...   
1977538 2022-04-19 17:43:43+00:00 2022-04-19 23:59:58+00:00   
1977539 2022-04-20 18:37:57+00:00 2022-04-20 23:59:58+00:00   
1977544 2022-04-25 18:38:20+00:00 2022-04-25 23:59:58+00:00   
1977546 2022-04-27 20:28:51+00:00 2022-04-27 23:59:58+00:00   
1980775 2022-06-10 12:54:44+00:00 2022-06-10 23:59:58+00:00   

         available_at_end_of_day  
248                        False  
3555                       False  
4699                       False  
15928                      False  
15929                      False  
...                          ...  
1977538                    False  
1977539                    False  
1977544                    False  
1977546                    False  
1980775                    False  

[10480 rows x 9 columns]

---

---

- # Code for stock out duration -- Product Wise

This part of code has been kept as a comment because we have impplemented a modified code whcich determines the same for all product together

In [30]:
'''

def get_stock_out(product_id, merged_sorted_availability):
    # Filter the data for the given product_id
    product_data = merged_sorted_availability[merged_sorted_availability['product_id'] == product_id]

    stock_out_list = []  # List to store stock_out tuples
    stock_out_start = None
    stock_out_end = None
    look_for_stock_out_end_from_same_row = True

    number_of_sale_days = len(product_data)
    index = 0

    flag = True

    # Iterating over the rows of product_data
    #for index in range(len(product_data)):
    while(index < number_of_sale_days):
        row = product_data.iloc[index]
        print("==============================================")
        print("current index of the while loop iteration", index)
        print("row", row)

        # Code for determining the stock_out_start
        print("--determining the stock_out_start--")
        if not row['available_at_start_of_day'] and flag == True:           #### if not available at start of day & flag = True
            stock_out_start = row['datetime_at_start_of_day']               # stock out start => at start of day
            look_for_stock_out_end_from_same_row = True
            print("Not available_at_start_of_day ==> Stock_out_start = datetime_at_start_of_day")
            print("Stock_out_start", stock_out_start)

            
        else:                                                               #### if available at start of day

            if row['available_at_end_of_day']:                              ## and available at end of day 
                look_for_stock_out_end_from_same_row = True                 # continue
                print("available_at_start_of_day and also available_at_end_of_day  ==> Continue search to next row")
                index= index + 1
                continue  

            else:                                                           ## and not available at end of day 
                if not pd.isnull(row['first_order_timestamp']):
                    stock_out_start = row['last_order_timestamp']           # stock out start => last order of day
                    look_for_stock_out_end_from_same_row = False
                    print("Not available_at_end_of_day and was sold during day ==> Stock_out_start set to last_order_timestamp")
                    print("Stock_out_start", stock_out_start)
                else:
                    stock_out_start = row['datetime_at_end_of_day']         # stock out start => at end of day
                    look_for_stock_out_end_from_same_row = False
                    print("Not available_at_end_of_day but was not sold during day ==> Stock_out_start set to datetime_at_end_of_day")
                    print("Stock_out_start", stock_out_start)


        # Code for determining the stock_out_end
        print("--determining the stock_out_end--")
        print("current index of the while loop iteration", index)
        print("row", row)


        # Initializing the start_index for nested for loop for determining the stock_out_end
        nested_index = index
        if look_for_stock_out_end_from_same_row:
            nested_index = index
        else:
            nested_index = index + 1

        print("nested index",nested_index)


        # Nested for loop 
        #for nested_index in range(nested_start_index, len(product_data)):
        while (nested_index < number_of_sale_days ):
            nested_row = product_data.iloc[nested_index]
            print("nested_index", nested_index, "nested_row", nested_row)

            if not pd.isnull(nested_row['first_order_timestamp']):                  #### if sold during the day
                stock_out_end = pd.Timestamp(nested_row['first_order_timestamp'])   # stock out end => first order of day
                print("Sold during the day ==> Stock_out_end set to first_order_timestamp")
                print("stock_out_end", stock_out_end)
                
                if nested_row['available_at_end_of_day']:
                    index = nested_index + 1  # start looking for the next stock out start from the next row
                    flag = True
                else:
                    index = nested_index # start looking for the next stock out start from the same row
                    flag = False

                break

            else:                                                                   #### if not sold during the day
                if nested_row['available_at_end_of_day']:                           ## and becomes available at end of day
                    stock_out_end = pd.Timestamp(nested_row['datetime_at_end_of_day']) # stock out end => at end of day
                    print("Not sold during the day but available at end of day ==> Stock_out_end set to datetime_at_end_of_day")
                    print("stock_out_end", stock_out_end)
                    index = nested_index + 1 # start looking for the nest stock out start from the next row
                    flag = True
                    break

                else:                                                               ## and does not become available at end of day
                    print("Not sold during the day and not available at end of day ==> Continue search to next nested_index and nested_row ")
                    nested_index = nested_index + 1
                    flag = True
                    continue                                                        # continue


        # adding the time stamps to the tuple list
        if stock_out_start is not None and stock_out_end is not None:
            if len(stock_out_list) > 0:
                previous_end = stock_out_list[-1][1]
                if pd.Timestamp(stock_out_start) >= previous_end:
                    stock_out_list.append((stock_out_start, stock_out_end))
            else:
                stock_out_list.append((stock_out_start, stock_out_end))

        # Reset stock_out_start and stock_out_end
        stock_out_start = None
        stock_out_end = None
        #look_for_stock_out_end_from_same_row = True


# Write the stock_out_list to a text document
    file_path = f"stock_out_timestamps_product_id_{product_id}.txt"
    with open(file_path, "w") as file:
        for stock_out_start, stock_out_end in stock_out_list:
            file.write(f"Stock out start: {stock_out_start}, Stock out end: {stock_out_end}\n") 
            
    print("Stock out list has been written to a text file.")
    print(stock_out_list)
    return stock_out_list

'''

'\n\ndef get_stock_out(product_id, merged_sorted_availability):\n    # Filter the data for the given product_id\n    product_data = merged_sorted_availability[merged_sorted_availability[\'product_id\'] == product_id]\n\n    stock_out_list = []  # List to store stock_out tuples\n    stock_out_start = None\n    stock_out_end = None\n    look_for_stock_out_end_from_same_row = True\n\n    number_of_sale_days = len(product_data)\n    index = 0\n\n    flag = True\n\n    # Iterating over the rows of product_data\n    #for index in range(len(product_data)):\n    while(index < number_of_sale_days):\n        row = product_data.iloc[index]\n        print("==============================================")\n        print("current index of the while loop iteration", index)\n        print("row", row)\n\n        # Code for determining the stock_out_start\n        print("--determining the stock_out_start--")\n        if not row[\'available_at_start_of_day\'] and flag == True:           #### if not avail

- get stock out --  saves the output timestamps into a text file

In [31]:
'''

# get_stock_out
get_stock_out('35',merged_sorted_availability)

'''

"\n\n# get_stock_out\nget_stock_out('35',merged_sorted_availability)\n\n"

- get product wise stock availability data -- saves the stock availability data into an excel

In [32]:
'''

# merged_sorted_availability product_id based selected rows

import csv

product_id = '35'  # Replace with the desired product_id

filtered_data = merged_sorted_availability.loc[merged_sorted_availability['product_id'] == product_id]

filename = f'filtered_data_{product_id}.csv'

filtered_data.to_csv(filename, index=False)

print(f'Filtered data for Product ID {product_id} has been written to {filename}')

'''

"\n\n# merged_sorted_availability product_id based selected rows\n\nimport csv\n\nproduct_id = '35'  # Replace with the desired product_id\n\nfiltered_data = merged_sorted_availability.loc[merged_sorted_availability['product_id'] == product_id]\n\nfilename = f'filtered_data_{product_id}.csv'\n\nfiltered_data.to_csv(filename, index=False)\n\nprint(f'Filtered data for Product ID {product_id} has been written to {filename}')\n\n"

---

---

- # Code for stock out duration -- All products together

writes to a csv

In [27]:

# Create an empty DataFrame to be populated
stock_out_all_products = pd.DataFrame(columns=['product_id', 'stock_out_timestamps'])

def get_stock_out_all_products(merged_sorted_availability, stock_out_all_products):
    
    # create a sorted list of unique product ids to iterate over
    product_id_all_products = merged_sorted_availability['product_id'].unique().tolist()

    # Convert numbers in the list to integers for sorting
    product_id_all_products = [int(x) for x in product_id_all_products]
    product_id_all_products.sort()

    # Convert numbers back to original data type
    product_id_all_products = [str(x) for x in product_id_all_products]


    #iteration over the list of product ids
    for product_id in product_id_all_products:
        #print("processing product_id",product_id)
        
        product_data = merged_sorted_availability[merged_sorted_availability['product_id'] == product_id]
    
        stock_out_list = []  # List to store stock_out tuples
        stock_out_start = None
        stock_out_end = None
        look_for_stock_out_end_from_same_row = True

        number_of_sale_days = len(product_data)
        index = 0

        flag = True

        # Iterating over the rows of product_data
        #for index in range(len(product_data)):
        while(index < number_of_sale_days):
            row = product_data.iloc[index]
            #print("==============================================")
            #print("current index of the while loop iteration", index)
            #print("row", row)

            # Code for determining the stock_out_start
            #print("--determining the stock_out_start--")
            if not row['available_at_start_of_day'] and flag == True:           #### if not available at start of day & flag = True
                stock_out_start = row['datetime_at_start_of_day']               # stock out start => at start of day
                look_for_stock_out_end_from_same_row = True
                #print("Not available_at_start_of_day ==> Stock_out_start = datetime_at_start_of_day")
                #print("Stock_out_start", stock_out_start)

                
            else:                                                               #### if available at start of day

                if row['available_at_end_of_day']:                              ## and available at end of day 
                    look_for_stock_out_end_from_same_row = True                 # continue
                    #print("available_at_start_of_day and also available_at_end_of_day  ==> Continue search to next row")
                    index= index + 1
                    continue  

                else:                                                           ## and not available at end of day 
                    if not pd.isnull(row['first_order_timestamp']):
                        stock_out_start = row['last_order_timestamp']           # stock out start => last order of day
                        look_for_stock_out_end_from_same_row = False
                        #print("Not available_at_end_of_day and was sold during day ==> Stock_out_start set to last_order_timestamp")
                        #print("Stock_out_start", stock_out_start)
                    else:
                        stock_out_start = row['datetime_at_end_of_day']         # stock out start => at end of day
                        look_for_stock_out_end_from_same_row = False
                        #print("Not available_at_end_of_day but was not sold during day ==> Stock_out_start set to datetime_at_end_of_day")
                        #print("Stock_out_start", stock_out_start)


            # Code for determining the stock_out_end
            #print("--determining the stock_out_end--")
            #print("current index of the while loop iteration", index)
            #print("row", row)


            # Initializing the start_index for nested for loop for determining the stock_out_end
            nested_index = index
            if look_for_stock_out_end_from_same_row:
                nested_index = index
            else:
                nested_index = index + 1

            #print("nested index",nested_index)


            # Nested for loop 
            #for nested_index in range(nested_start_index, len(product_data)):
            while (nested_index < number_of_sale_days ):
                nested_row = product_data.iloc[nested_index]
                #print("nested_index", nested_index, "nested_row", nested_row)

                if not pd.isnull(nested_row['first_order_timestamp']):                  #### if sold during the day
                    stock_out_end = pd.Timestamp(nested_row['first_order_timestamp'])   # stock out end => first order of day
                    #print("Sold during the day ==> Stock_out_end set to first_order_timestamp")
                    #print("stock_out_end", stock_out_end)
                    
                    if nested_row['available_at_end_of_day']:
                        index = nested_index + 1  # start looking for the next stock out start from the next row
                        flag = True
                    else:
                        index = nested_index # start looking for the next stock out start from the same row
                        flag = False

                    break

                else:                                                                   #### if not sold during the day
                    if nested_row['available_at_end_of_day']:                           ## and becomes available at end of day
                        stock_out_end = pd.Timestamp(nested_row['datetime_at_end_of_day']) # stock out end => at end of day
                        #print("Not sold during the day but available at end of day ==> Stock_out_end set to datetime_at_end_of_day")
                        #print("stock_out_end", stock_out_end)
                        index = nested_index + 1 # start looking for the nest stock out start from the next row
                        flag = True
                        break

                    else:                                                               ## and does not become available at end of day
                        #print("Not sold during the day and not available at end of day ==> Continue search to next nested_index and nested_row ")
                        nested_index = nested_index + 1
                        flag = True
                        continue                                                        # continue


            # adding the time stamps to the tuple list
            if stock_out_start is not None and stock_out_end is not None:
                if len(stock_out_list) > 0:
                    previous_end = stock_out_list[-1][1]
                    if pd.Timestamp(stock_out_start) >= previous_end:
                        stock_out_list.append((stock_out_start, stock_out_end))
                else:
                    stock_out_list.append((stock_out_start, stock_out_end))

            # Reset stock_out_start and stock_out_end
            stock_out_start = None
            stock_out_end = None
            #look_for_stock_out_end_from_same_row = True

        
        # Append the stock_out_list to stock_out_all_products DataFrame
        stock_out_all_products = stock_out_all_products.append(
            {'product_id': product_id, 'stock_out_timestamps': stock_out_list}, ignore_index=True)

    return stock_out_all_products




In [28]:
# Call the function and pass the empty DataFrame as an argument (takes 11min)
stock_out_all_products = get_stock_out_all_products(merged_sorted_availability, stock_out_all_products)


-  EDA on the stock_out_all_products

In [29]:
stock_out_all_products.head(10)

product_id                               stock_out_timestamps
0          0  [(2022-01-01 09:30:44+00:00, 2022-01-07 21:04:...
1          1  [(2022-07-18 17:29:21+00:00, 2023-03-31 23:59:...
2          2                                                 []
3          3  [(2022-01-01 17:57:57+00:00, 2022-01-04 17:59:...
4          4  [(2022-01-01 00:00:01+00:00, 2022-05-23 23:59:...
5          5  [(2022-01-01 00:00:01+00:00, 2022-07-20 23:59:...
6          6  [(2023-01-29 19:27:39+00:00, 2023-03-31 23:59:...
7          7  [(2022-01-01 00:00:01+00:00, 2023-01-06 06:01:...
8          8  [(2022-01-01 00:00:01+00:00, 2022-02-12 23:59:...
9          9  [(2022-07-23 23:59:58+00:00, 2022-08-01 23:59:...

- Adding additonal columns to the dataframe stock_out_all_products

In [30]:
# Calculate stock_out_duration corresponding to each stock out instance

stock_out_all_products['stock_out_duration_hours'] = stock_out_all_products['stock_out_timestamps'].apply(lambda x: [((pd.to_datetime(end) - pd.to_datetime(start)).total_seconds() / 3600) for start, end in x])

stock_out_all_products['stock_out_days'] = stock_out_all_products['stock_out_timestamps'].apply(lambda x: [((pd.to_datetime(end) - pd.to_datetime(start)).days) for start, end in x])

stock_out_all_products['total_stock_out_hours'] = stock_out_all_products['stock_out_duration_hours'].apply(lambda x: sum(x))


In [31]:
stock_out_all_products

product_id                               stock_out_timestamps  \
0             0  [(2022-01-01 09:30:44+00:00, 2022-01-07 21:04:...   
1             1  [(2022-07-18 17:29:21+00:00, 2023-03-31 23:59:...   
2             2                                                 []   
3             3  [(2022-01-01 17:57:57+00:00, 2022-01-04 17:59:...   
4             4  [(2022-01-01 00:00:01+00:00, 2022-05-23 23:59:...   
...         ...                                                ...   
4355       4358  [(2022-02-13 17:29:16+00:00, 2022-02-15 23:59:...   
4356       4359  [(2022-01-01 00:00:01+00:00, 2022-01-12 23:59:...   
4357       4360  [(2022-01-01 00:00:01+00:00, 2022-03-04 23:59:...   
4358       4361  [(2022-08-21 13:58:45+00:00, 2022-08-23 23:59:...   
4359       4362  [(2022-01-04 13:35:41+00:00, 2022-01-27 23:59:...   

                               stock_out_duration_hours  \
0     [155.55944444444444, 114.26972222222223, 48.13...   
1                                   [6150.510277777777]   
2                                                    []   
3     [72.02055555555556, 41.15138888888889, 24.6333...   
4                                  [3431.9991666666665]   
...                                                 ...   
4355  [54.51166666666666, 96.0, 77.62916666666666, 6...   
4356  [287.99916666666667, 150.58333333333334, 71.73...   
4357  [1511.9991666666667, 74.05361111111111, 3029.6...   
4358             [58.02027777777778, 96.13277777777778]   
4359  [562.4047222222222, 93.10055555555556, 35.5091...   

                                     stock_out_days  total_stock_out_hours  
0     [6, 4, 2, 4, 1, 2, 7, 2, 0, 2, 2, 3, 0, 6, 0]            1182.800278  
1                                             [256]            6150.510278  
2                                                []               0.000000  
3                             [3, 1, 1, 1, 3, 3, 2]             402.141389  
4                                             [142]            3431.999167  
...                                             ...                    ...  
4355                            [2, 4, 3, 2, 3, 73]            2135.317222  
4356                                     [11, 6, 2]             510.320556  
4357                                   [62, 3, 126]            4615.661667  
4358                                         [2, 4]             154.153056  
4359                                     [23, 3, 1]             691.014444  

[4360 rows x 5 columns]

In [32]:
# Write the updated DataFrame to the CSV file
stock_out_all_products.to_csv('stock_out_all_products.csv', index=False, mode='w')

---

---

# Code for creating order level stock out status -- Of All products corresponding to an order

- Create a copy of stock_out_all_products dataframe

In [38]:
df_copy_stock_out_all_products = stock_out_all_products.copy()

In [39]:
df_copy_stock_out_all_products

product_id                               stock_out_timestamps  \
0             0  [(2022-01-01 09:30:44+00:00, 2022-01-07 21:04:...   
1             1  [(2022-07-18 17:29:21+00:00, 2023-03-31 23:59:...   
2             2                                                 []   
3             3  [(2022-01-01 17:57:57+00:00, 2022-01-04 17:59:...   
4             4  [(2022-01-01 00:00:01+00:00, 2022-05-23 23:59:...   
...         ...                                                ...   
4355       4358  [(2022-02-13 17:29:16+00:00, 2022-02-15 23:59:...   
4356       4359  [(2022-01-01 00:00:01+00:00, 2022-01-12 23:59:...   
4357       4360  [(2022-01-01 00:00:01+00:00, 2022-03-04 23:59:...   
4358       4361  [(2022-08-21 13:58:45+00:00, 2022-08-23 23:59:...   
4359       4362  [(2022-01-04 13:35:41+00:00, 2022-01-27 23:59:...   

                               stock_out_duration_hours  \
0     [155.55944444444444, 114.26972222222223, 48.13...   
1                                   [6150.510277777777]   
2                                                    []   
3     [72.02055555555556, 41.15138888888889, 24.6333...   
4                                  [3431.9991666666665]   
...                                                 ...   
4355  [54.51166666666666, 96.0, 77.62916666666666, 6...   
4356  [287.99916666666667, 150.58333333333334, 71.73...   
4357  [1511.9991666666667, 74.05361111111111, 3029.6...   
4358             [58.02027777777778, 96.13277777777778]   
4359  [562.4047222222222, 93.10055555555556, 35.5091...   

                                     stock_out_days  total_stock_out_hours  
0     [6, 4, 2, 4, 1, 2, 7, 2, 0, 2, 2, 3, 0, 6, 0]            1182.800278  
1                                             [256]            6150.510278  
2                                                []               0.000000  
3                             [3, 1, 1, 1, 3, 3, 2]             402.141389  
4                                             [142]            3431.999167  
...                                             ...                    ...  
4355                            [2, 4, 3, 2, 3, 73]            2135.317222  
4356                                     [11, 6, 2]             510.320556  
4357                                   [62, 3, 126]            4615.661667  
4358                                         [2, 4]             154.153056  
4359                                     [23, 3, 1]             691.014444  

[4360 rows x 5 columns]

- Create a copy of the sorted_sales dataframe

In [40]:
df_copy_sorted_sales = sorted_sales.copy()

# sort by order id
df_copy_sorted_sales = df_copy_sorted_sales.sort_values('order_id')


In [41]:
df_copy_sorted_sales.head(10)

order_id store_id  order_date product_id customer_id  \
573487        0        0  2022-09-12       3834       13304   
295013        1        0  2022-11-22       2495       11820   
672747        1        0  2022-11-22       4271       11820   
614752        1        0  2022-11-22       4031       11820   
274441       10        0  2022-02-06       2371        5839   
285287       10        0  2022-02-06       2445        5839   
447194       10        0  2022-02-06       3225        5839   
441247       10        0  2022-02-06       3193        5839   
302282       10        0  2022-02-06       2529        5839   
528776       10        0  2022-02-06       3599        5839   

                                             product_name  sold_quantity  \
573487                                   Agua Bezoya 1.5L            8.0   
295013              Barilla Pasta Spaghetti Integral 500g            1.0   
672747          Carbonell Aceite de Oliva Virgen Extra 1L            1.0   
614752  Ariel 3en1 Pods Original Detergente Cápsulas 1...            1.0   
274441                          Milka Oreo chocolate 100g            1.0   
285287  Pack Helado Ben&Jerry's Choco Brownie&Cookie D...            1.0   
447194                       Milka galleta chocolate 300g            1.0   
441247                     Haribo Mega Torcidas Fresa 75g            1.0   
302282            Ben & Jerry's Helado Cookie Dough 465ml            1.0   
528776  Ben & Jerry's Helado Chocolate Fudge Brownie 4...            1.0   

                  order_datetime     first_order_timestamp  \
573487 2022-09-12 10:27:01+00:00 2022-09-12 07:01:26+00:00   
295013 2022-11-22 17:39:21+00:00 2022-11-22 17:39:21+00:00   
672747 2022-11-22 17:39:21+00:00 2022-11-22 07:29:53+00:00   
614752 2022-11-22 17:39:21+00:00 2022-11-22 17:39:21+00:00   
274441 2022-02-06 21:15:39+00:00 2022-02-06 16:20:57+00:00   
285287 2022-02-06 21:15:39+00:00 2022-02-06 21:15:39+00:00   
447194 2022-02-06 21:15:39+00:00 2022-02-06 18:10:32+00:00   
441247 2022-02-06 21:15:39+00:00 2022-02-06 17:35:31+00:00   
302282 2022-02-06 21:15:39+00:00 2022-02-06 01:24:33+00:00   
528776 2022-02-06 21:15:39+00:00 2022-02-06 12:09:47+00:00   

            last_order_timestamp  
573487 2022-09-12 22:13:05+00:00  
295013 2022-11-22 17:39:21+00:00  
672747 2022-11-22 17:39:21+00:00  
614752 2022-11-22 17:39:21+00:00  
274441 2022-02-06 21:15:39+00:00  
285287 2022-02-06 21:29:05+00:00  
447194 2022-02-06 21:15:39+00:00  
441247 2022-02-06 21:15:39+00:00  
302282 2022-02-06 22:17:13+00:00  
528776 2022-02-06 22:58:54+00:00

- Creating a list of order_id and the products contained in the order

In [42]:
order_wise_product_ids = []

for order_id, group in df_copy_sorted_sales.groupby('order_id'):
    product_ids = group['product_id'].tolist()
    order_dict = {'order_id': order_id, 'products': product_ids}
    order_wise_product_ids.append(order_dict)


In [43]:
order_wise_product_ids

[{'order_id': '0', 'products': ['3834']},
 {'order_id': '1', 'products': ['2495', '4271', '4031']},
 {'order_id': '10',
  'products': ['2371', '2445', '3225', '3193', '2529', '3599', '3181']},
 {'order_id': '100',
  'products': ['2385', '201', '291', '1764', '2156', '688', '602', '4302']},
 {'order_id': '1000', 'products': ['3165', '1344', '2512', '2571', '4317']},
 {'order_id': '10000', 'products': ['3834', '3047']},
 {'order_id': '100000', 'products': ['780', '789', '345', '3405']},
 {'order_id': '100001', 'products': ['2667', '3385']},
 {'order_id': '100002', 'products': ['1640', '4328', '4326']},
 {'order_id': '100003', 'products': ['4144', '1279']},
 {'order_id': '100004',
  'products': ['1786', '1178', '3668', '1948', '667', '3527']},
 {'order_id': '100005', 'products': ['3068', '1302', '719']},
 {'order_id': '100006',
  'products': ['2839', '248', '3360', '1573', '3617', '3335', '3893', '4097']},
 {'order_id': '100007',
  'products': ['842',
   '2668',
   '4081',
   '4280',
   '

- We need to drop the duplicates as we need only the timestamp of unique order ids

In [44]:
# checking the number of unique order ids
unique_order_count = df_copy_sorted_sales['order_id'].nunique()
print(unique_order_count)

162819


In [45]:
# dropping duplicates and verifying that the updated dataframe has same number of rows as the number of unique orders
df_copy_sorted_sales = df_copy_sorted_sales.drop_duplicates(subset='order_id')
df_copy_sorted_sales

order_id store_id  order_date product_id customer_id  \
573487        0        0  2022-09-12       3834       13304   
295013        1        0  2022-11-22       2495       11820   
274441       10        0  2022-02-06       2371        5839   
276643      100        0  2022-03-11       2385       32264   
437067     1000        0  2023-01-26       3165       27021   
...         ...      ...         ...        ...         ...   
276814    99995        0  2022-08-07       2387       13292   
351559    99996        0  2022-11-18        275        7593   
451265    99997        0  2022-04-21       3261       28268   
55946     99998        0  2022-10-10       1279       19914   
538339    99999        0  2022-01-25       3667         537   

                                            product_name  sold_quantity  \
573487                                  Agua Bezoya 1.5L            8.0   
295013             Barilla Pasta Spaghetti Integral 500g            1.0   
274441                         Milka Oreo chocolate 100g            1.0   
276643                       Millán Vicente Edam + Gouda            1.0   
437067                      Granini zumo 100% fruta piña            2.0   
...                                                  ...            ...   
276814  Conguitos Cups Rellenos de Crema de Cacahuete 6u            1.0   
351559                     Coronita Cerveza Extra 35.5cl            6.0   
451265  Coca-Cola Zero Azúcar Zero Cafeína botella 500ml            2.0   
55946                          Agua Solán de Cabras 1.5L            6.0   
538339                        Pascual Leche Desnatada 1l            6.0   

                  order_datetime     first_order_timestamp  \
573487 2022-09-12 10:27:01+00:00 2022-09-12 07:01:26+00:00   
295013 2022-11-22 17:39:21+00:00 2022-11-22 17:39:21+00:00   
274441 2022-02-06 21:15:39+00:00 2022-02-06 16:20:57+00:00   
276643 2022-03-11 09:28:00+00:00 2022-03-11 09:28:00+00:00   
437067 2023-01-26 19:54:18+00:00 2023-01-26 19:54:18+00:00   
...                          ...                       ...   
276814 2022-08-07 21:37:02+00:00 2022-08-07 21:37:02+00:00   
351559 2022-11-18 22:16:28+00:00 2022-11-18 12:41:22+00:00   
451265 2022-04-21 20:07:08+00:00 2022-04-21 08:22:30+00:00   
55946  2022-10-10 15:50:09+00:00 2022-10-10 06:54:55+00:00   
538339 2022-01-25 21:04:03+00:00 2022-01-25 11:54:48+00:00   

            last_order_timestamp  
573487 2022-09-12 22:13:05+00:00  
295013 2022-11-22 17:39:21+00:00  
274441 2022-02-06 21:15:39+00:00  
276643 2022-03-11 17:21:30+00:00  
437067 2023-01-26 19:54:18+00:00  
...                          ...  
276814 2022-08-07 21:37:02+00:00  
351559 2022-11-18 23:59:27+00:00  
451265 2022-04-21 20:07:08+00:00  
55946  2022-10-10 22:35:36+00:00  
538339 2022-01-25 21:04:03+00:00  

[162819 rows x 10 columns]

- Creating a list of timestamps of the order

In [46]:
order_wise_timestamps = []

grouped_data = df_copy_sorted_sales.groupby('order_id')

for order_id, group in grouped_data:
    order_dict = {'order_id': int(order_id), 'order_datetime': group['order_datetime'].tolist()}
    order_wise_timestamps.append(order_dict)

In [47]:
order_wise_timestamps

[{'order_id': 0,
  'order_datetime': [Timestamp('2022-09-12 10:27:01+0000', tz='UTC')]},
 {'order_id': 1,
  'order_datetime': [Timestamp('2022-11-22 17:39:21+0000', tz='UTC')]},
 {'order_id': 10,
  'order_datetime': [Timestamp('2022-02-06 21:15:39+0000', tz='UTC')]},
 {'order_id': 100,
  'order_datetime': [Timestamp('2022-03-11 09:28:00+0000', tz='UTC')]},
 {'order_id': 1000,
  'order_datetime': [Timestamp('2023-01-26 19:54:18+0000', tz='UTC')]},
 {'order_id': 10000,
  'order_datetime': [Timestamp('2022-07-30 19:28:36+0000', tz='UTC')]},
 {'order_id': 100000,
  'order_datetime': [Timestamp('2023-03-25 09:08:47+0000', tz='UTC')]},
 {'order_id': 100001,
  'order_datetime': [Timestamp('2022-01-31 22:00:02+0000', tz='UTC')]},
 {'order_id': 100002,
  'order_datetime': [Timestamp('2022-08-28 20:17:21+0000', tz='UTC')]},
 {'order_id': 100003,
  'order_datetime': [Timestamp('2022-05-17 19:18:02+0000', tz='UTC')]},
 {'order_id': 100004,
  'order_datetime': [Timestamp('2023-01-01 16:21:23+0000',

- Code -> creates a dataframe order_wise_out_of_stock_product_ids (takes 30mins)

In [48]:
import pandas as pd

order_wise_out_of_stock_product_ids = []
count = 0

for _, row in df_copy_sorted_sales.iterrows(): # we have already dropped the duplicates
    
    order_id = row['order_id']
    order_datetime = row['order_datetime']
    print("order_id count ", count) # to track the progress It took 23 minutes
    
    out_of_stock_mask = df_copy_stock_out_all_products['stock_out_timestamps'].apply(
        lambda timestamps: any(stock_out_start <= order_datetime <= stock_out_end for stock_out_start, stock_out_end in timestamps)
        # since its <= and <= therefore and the code does not include the products which correspond to the order itself , those products are also included
    )
    out_of_stock_products = df_copy_stock_out_all_products.loc[out_of_stock_mask, 'product_id'].tolist()
    
    order_wise_out_of_stock_product_ids.append({'order_id': order_id,'order_datetime':order_datetime, 'out_of_stock_products': out_of_stock_products})

    count = count + 1

# Create the dataframe from the collected data
order_wise_out_of_stock_product_ids = pd.DataFrame(order_wise_out_of_stock_product_ids)

order_id count  0
order_id count  1
order_id count  2
order_id count  3
order_id count  4
order_id count  5
order_id count  6
order_id count  7
order_id count  8
order_id count  9
order_id count  10
order_id count  11
order_id count  12
order_id count  13
order_id count  14
order_id count  15
order_id count  16
order_id count  17
order_id count  18
order_id count  19
order_id count  20
order_id count  21
order_id count  22
order_id count  23
order_id count  24
order_id count  25
order_id count  26
order_id count  27
order_id count  28
order_id count  29
order_id count  30
order_id count  31
order_id count  32
order_id count  33
order_id count  34
order_id count  35
order_id count  36
order_id count  37
order_id count  38
order_id count  39
order_id count  40
order_id count  41
order_id count  42
order_id count  43
order_id count  44
order_id count  45
order_id count  46
order_id count  47
order_id count  48
order_id count  49
order_id count  50
order_id count  51
order_id count  52
ord

In [49]:
order_wise_out_of_stock_product_ids

order_id            order_datetime  \
0             0 2022-09-12 10:27:01+00:00   
1             1 2022-11-22 17:39:21+00:00   
2            10 2022-02-06 21:15:39+00:00   
3           100 2022-03-11 09:28:00+00:00   
4          1000 2023-01-26 19:54:18+00:00   
...         ...                       ...   
162814    99995 2022-08-07 21:37:02+00:00   
162815    99996 2022-11-18 22:16:28+00:00   
162816    99997 2022-04-21 20:07:08+00:00   
162817    99998 2022-10-10 15:50:09+00:00   
162818    99999 2022-01-25 21:04:03+00:00   

                                    out_of_stock_products  
0       [1, 5, 7, 8, 9, 10, 11, 13, 15, 20, 23, 24, 25...  
1       [1, 7, 8, 10, 11, 13, 15, 20, 24, 25, 26, 27, ...  
2       [4, 5, 7, 8, 10, 13, 14, 15, 18, 20, 22, 23, 2...  
3       [4, 5, 7, 8, 10, 13, 15, 18, 20, 22, 23, 24, 2...  
4       [1, 5, 7, 8, 10, 11, 12, 17, 20, 26, 28, 32, 3...  
...                                                   ...  
162814  [1, 7, 8, 10, 11, 13, 15, 20, 23, 24, 25, 26, ...  
162815  [1, 7, 8, 10, 11, 13, 15, 20, 24, 25, 26, 27, ...  
162816  [4, 5, 7, 8, 10, 13, 15, 20, 22, 23, 24, 25, 2...  
162817  [1, 5, 7, 8, 10, 11, 13, 15, 20, 23, 24, 25, 2...  
162818  [4, 5, 7, 8, 10, 12, 13, 14, 15, 18, 20, 22, 2...  

[162819 rows x 3 columns]

In [50]:
order_wise_product_ids

[{'order_id': '0', 'products': ['3834']},
 {'order_id': '1', 'products': ['2495', '4271', '4031']},
 {'order_id': '10',
  'products': ['2371', '2445', '3225', '3193', '2529', '3599', '3181']},
 {'order_id': '100',
  'products': ['2385', '201', '291', '1764', '2156', '688', '602', '4302']},
 {'order_id': '1000', 'products': ['3165', '1344', '2512', '2571', '4317']},
 {'order_id': '10000', 'products': ['3834', '3047']},
 {'order_id': '100000', 'products': ['780', '789', '345', '3405']},
 {'order_id': '100001', 'products': ['2667', '3385']},
 {'order_id': '100002', 'products': ['1640', '4328', '4326']},
 {'order_id': '100003', 'products': ['4144', '1279']},
 {'order_id': '100004',
  'products': ['1786', '1178', '3668', '1948', '667', '3527']},
 {'order_id': '100005', 'products': ['3068', '1302', '719']},
 {'order_id': '100006',
  'products': ['2839', '248', '3360', '1573', '3617', '3335', '3893', '4097']},
 {'order_id': '100007',
  'products': ['842',
   '2668',
   '4081',
   '4280',
   '

In [51]:
# Create a dictionary from the order_wise_product_ids list for efficient lookup
order_product_dict = {item['order_id']: item['products'] for item in order_wise_product_ids}

# Add a new column 'products_contained_in_order' to the DataFrame
order_wise_out_of_stock_product_ids['products_contained_in_order'] = order_wise_out_of_stock_product_ids['order_id'].map(order_product_dict)


In [132]:
order_wise_out_of_stock_product_ids['order_id'] = order_wise_out_of_stock_product_ids['order_id'].astype(str)


In [133]:
# Display dataframe
order_wise_out_of_stock_product_ids.head(10)


order_id            order_datetime  \
0        0 2022-09-12 10:27:01+00:00   
1        1 2022-11-22 17:39:21+00:00   
2       10 2022-02-06 21:15:39+00:00   
3      100 2022-03-11 09:28:00+00:00   
4     1000 2023-01-26 19:54:18+00:00   
5    10000 2022-07-30 19:28:36+00:00   
6   100000 2023-03-25 09:08:47+00:00   
7   100001 2022-01-31 22:00:02+00:00   
8   100002 2022-08-28 20:17:21+00:00   
9   100003 2022-05-17 19:18:02+00:00   

                               out_of_stock_products  \
0  [1, 5, 7, 8, 9, 10, 11, 13, 15, 20, 23, 24, 25...   
1  [1, 7, 8, 10, 11, 13, 15, 20, 24, 25, 26, 27, ...   
2  [4, 5, 7, 8, 10, 13, 14, 15, 18, 20, 22, 23, 2...   
3  [4, 5, 7, 8, 10, 13, 15, 18, 20, 22, 23, 24, 2...   
4  [1, 5, 7, 8, 10, 11, 12, 17, 20, 26, 28, 32, 3...   
5  [1, 7, 8, 9, 10, 11, 13, 15, 20, 23, 24, 25, 2...   
6  [1, 5, 6, 7, 8, 10, 11, 12, 17, 19, 26, 28, 29...   
7  [4, 5, 7, 8, 10, 11, 12, 13, 14, 15, 18, 20, 2...   
8  [1, 7, 8, 10, 11, 13, 15, 20, 23, 24, 25, 26, ...   
9  [4, 5, 7, 8, 10, 13, 15, 20, 22, 23, 24, 25, 2...   

                    products_contained_in_order  
0                                        [3834]  
1                            [2495, 4271, 4031]  
2    [2371, 2445, 3225, 3193, 2529, 3599, 3181]  
3  [2385, 201, 291, 1764, 2156, 688, 602, 4302]  
4                [3165, 1344, 2512, 2571, 4317]  
5                                  [3834, 3047]  
6                         [780, 789, 345, 3405]  
7                                  [2667, 3385]  
8                            [1640, 4328, 4326]  
9                                  [4144, 1279]

In [54]:
# Write the updated DataFrame to the CSV file
order_wise_out_of_stock_product_ids.to_csv('order_level_out_of_stock_df.csv', index=False, mode='w')

---

---

In [136]:
import pandas as pd

# Read the CSV file
order_wise_out_of_stock_product_ids = pd.read_csv('order_level_out_of_stock_df.csv')

# Convert the datatype of order_id from int to str
order_wise_out_of_stock_product_ids['order_id'] = order_wise_out_of_stock_product_ids['order_id'].astype(str)

# Display the DataFrame
order_wise_out_of_stock_product_ids.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 162819 entries, 0 to 162818
Data columns (total 4 columns):
 #   Column                       Non-Null Count   Dtype 
---  ------                       --------------   ----- 
 0   order_id                     162819 non-null  object
 1   order_datetime               162819 non-null  object
 2   out_of_stock_products        162819 non-null  object
 3   products_contained_in_order  162819 non-null  object
dtypes: object(4)
memory usage: 5.0+ MB


In [137]:
# Display the dataframe
order_wise_out_of_stock_product_ids.head()


order_id             order_datetime  \
0        0  2022-09-12 10:27:01+00:00   
1        1  2022-11-22 17:39:21+00:00   
2       10  2022-02-06 21:15:39+00:00   
3      100  2022-03-11 09:28:00+00:00   
4     1000  2023-01-26 19:54:18+00:00   

                               out_of_stock_products  \
0  ['1', '5', '7', '8', '9', '10', '11', '13', '1...   
1  ['1', '7', '8', '10', '11', '13', '15', '20', ...   
2  ['4', '5', '7', '8', '10', '13', '14', '15', '...   
3  ['4', '5', '7', '8', '10', '13', '15', '18', '...   
4  ['1', '5', '7', '8', '10', '11', '12', '17', '...   

                         products_contained_in_order  
0                                           ['3834']  
1                           ['2495', '4271', '4031']  
2  ['2371', '2445', '3225', '3193', '2529', '3599...  
3  ['2385', '201', '291', '1764', '2156', '688', ...  
4           ['3165', '1344', '2512', '2571', '4317']

---

---

# Creating a function to convert product id into name and vice versa 

- Loading df_product_id_and_name (created by notebook 1) from csv and defining a function to convert id to name and vice versa

In [4]:
import pandas as pd

# Read the CSV file into a DataFrame
df_product_id_and_name_123 = pd.read_csv('df_product_id_and_name.csv')

#df_product_id_and_name_123

In [5]:
# function to convert id to name and vice versa

def get_product_name(product_id,df_product_id_and_name_123):
    # Search for the product name corresponding to the given product ID
    product_name = df_product_id_and_name_123[df_product_id_and_name_123['product_id'] == product_id]['product_name'].iloc[0]
    print("product_id",product_id,"product_name",product_name)
    return product_name

def get_product_id(product_name,df_product_id_and_name_123):
    # Search for the product ID corresponding to the given product name
    product_id = df_product_id_and_name_123[df_product_id_and_name_123['product_name'] == product_name]['product_id'].iloc[0]
    print("product_id",product_id,"product_name",product_name)
    return product_id


# Example
#get_product_name(4143,df_product_id_and_name_123)


---

---

# Choosing the subset of problematic products (X)

    These should be products with high frequency of orders ; having stock outs ; co-occuring with a lot of products when considering all the orders


- Loading the csv product_wise_qtysold_orderfreq_df (created by Notebook 1)

In [203]:
import pandas as pd

# Read the CSV file into a DataFrame
product_wise_qtysold_orderfreq_df = pd.read_csv('product_wise_qtysold_orderfreq_df.csv')

#product_wise_qtysold_orderfreq_df


- Loading the csv stock_out_all_products (created by this notebook)

In [15]:
# Read the CSV file into a DataFrame
stock_out_all_products = pd.read_csv('stock_out_all_products.csv')

# Drop the unnamed columns
stock_out_all_products = stock_out_all_products.drop(columns=stock_out_all_products.columns[stock_out_all_products.columns.str.contains('Unnamed:')])

# Display the updated DataFrame
stock_out_all_products


product_id                               stock_out_timestamps  \
0              0  [(Timestamp('2022-01-01 09:30:44+0000', tz='UT...   
1              1  [(Timestamp('2022-07-18 17:29:21+0000', tz='UT...   
2              2                                                 []   
3              3  [(Timestamp('2022-01-01 17:57:57+0000', tz='UT...   
4              4  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
...          ...                                                ...   
4355        4358  [(Timestamp('2022-02-13 17:29:16+0000', tz='UT...   
4356        4359  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
4357        4360  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
4358        4361  [(Timestamp('2022-08-21 13:58:45+0000', tz='UT...   
4359        4362  [(Timestamp('2022-01-04 13:35:41+0000', tz='UT...   

                               stock_out_duration_hours  \
0     [155.55944444444444, 114.26972222222223, 48.13...   
1                                   [6150.510277777777]   
2                                                    []   
3     [72.02055555555556, 41.15138888888889, 24.6333...   
4                                  [3431.9991666666665]   
...                                                 ...   
4355  [54.51166666666666, 96.0, 77.62916666666666, 6...   
4356  [287.99916666666667, 150.58333333333334, 71.73...   
4357  [1511.9991666666667, 74.05361111111111, 3029.6...   
4358             [58.02027777777778, 96.13277777777778]   
4359  [562.4047222222222, 93.10055555555556, 35.5091...   

                                     stock_out_days  total_stock_out_hours  
0     [6, 4, 2, 4, 1, 2, 7, 2, 0, 2, 2, 3, 0, 6, 0]            1182.800278  
1                                             [256]            6150.510278  
2                                                []               0.000000  
3                             [3, 1, 1, 1, 3, 3, 2]             402.141389  
4                                             [142]            3431.999167  
...                                             ...                    ...  
4355                            [2, 4, 3, 2, 3, 73]            2135.317222  
4356                                     [11, 6, 2]             510.320556  
4357                                   [62, 3, 126]            4615.661667  
4358                                         [2, 4]             154.153056  
4359                                     [23, 3, 1]             691.014444  

[4360 rows x 5 columns]

- Merging the product_wise_qtysold_orderfreq_df into stock_out_all_products

In [207]:
# Merge the dataframes based on 'product_id'
merged_df_123 = stock_out_all_products.merge(product_wise_qtysold_orderfreq_df, on='product_id', how='left')

# Display the merged dataframe with additional columns
#merged_df_123


- Drop the rows having null values in mentioined columns : ['stock_out_days', 'total_stock_out_hours', 'total_quantity_sold', 'total_order_ids']

In [213]:
# Filter the dataframe for non-null values in the specified columns
filtered_df_123 = merged_df_123.dropna(subset=['stock_out_days', 'total_stock_out_hours', 'total_quantity_sold', 'total_order_ids'])

# Drop rows with empty lists in stock_out_days column
filtered_df_123 = filtered_df_123[filtered_df_123['stock_out_days'].astype(bool)]

# Drop rows with 0.0 in total_stock_out_hours column
filtered_df_123 = filtered_df_123[filtered_df_123['total_stock_out_hours'] != 0.0]


- Sorted dataframe to see the high order frequency products

In [218]:
# Sort the filtered dataframe by total_order_ids 
sorted_df_123_by_frequency_of_orders = filtered_df_123.sort_values(by='total_order_ids', ascending= False)

# Display the sorted dataframe
sorted_df_123_by_frequency_of_orders.head(10)

product_id                               stock_out_timestamps  \
3831        3834  [(Timestamp('2022-01-07 13:23:27+0000', tz='UT...   
666          667  [(Timestamp('2022-01-02 21:32:28+0000', tz='UT...   
1278        1279  [(Timestamp('2022-01-02 08:06:40+0000', tz='UT...   
3520        3523  [(Timestamp('2022-04-12 18:30:20+0000', tz='UT...   
1279        1280  [(Timestamp('2022-06-12 05:46:45+0000', tz='UT...   
4141        4144  [(Timestamp('2022-01-06 19:44:33+0000', tz='UT...   
527          528  [(Timestamp('2022-01-03 18:11:58+0000', tz='UT...   
2666        2668  [(Timestamp('2022-01-02 12:28:41+0000', tz='UT...   
718          719  [(Timestamp('2022-01-07 20:13:13+0000', tz='UT...   
1306        1307  [(Timestamp('2022-01-03 20:10:57+0000', tz='UT...   

                               stock_out_duration_hours  \
3831  [40.56305555555556, 28.380555555555556, 23.984...   
666   [49.16833333333334, 26.703055555555554, 21.777...   
1278  [63.888333333333335, 13.26361111111111, 15.25,...   
3520  [20.774166666666666, 375.21472222222224, 41.57...   
1279  [56.4325, 45.20722222222222, 60.37972222222222...   
4141  [113.37444444444445, 13.369166666666667, 11.24...   
527   [21.503888888888888, 90.01638888888888, 21.968...   
2666  [22.269444444444446, 37.99194444444444, 24.607...   
718            [19.280555555555555, 20.906666666666666]   
1306  [27.816944444444445, 17.39027777777778, 18.466...   

                                         stock_out_days  \
3831                              [1, 1, 0, 4, 0, 0, 0]   
666                                        [2, 1, 0, 7]   
1278                                       [2, 0, 0, 2]   
3520                             [0, 15, 1, 3, 1, 0, 2]   
1279                                    [2, 1, 2, 1, 0]   
4141                                       [4, 0, 0, 0]   
527                                        [0, 3, 0, 3]   
2666  [0, 1, 1, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1, ...   
718                                              [0, 0]   
1306                              [1, 0, 0, 1, 3, 4, 5]   

      total_stock_out_hours  total_quantity_sold  total_order_ids  
3831             243.190833              60219.0            14756  
666              284.201944              65290.0            14096  
1278             159.075833              31285.0             7945  
3520             602.703056               7918.0             6420  
1279             212.815556              66201.0             6195  
4141             161.933056              42279.0             6161  
527              206.813611              25835.0             4996  
2666            5104.318333               5110.0             4678  
718               40.187222              46276.0             4522  
1306             426.377778               4376.0             4242

- Sorted dataframe to see the high stock out products

In [219]:
# Sort the filtered dataframe by total_stock_out_hours
sorted_df_123_by_total_stock_out_hours = filtered_df_123.sort_values(by='total_stock_out_hours', ascending= False)

# Display the sorted dataframe
sorted_df_123_by_total_stock_out_hours.head(10)

product_id                               stock_out_timestamps  \
1520        1522  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
4267        4270  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
2704        2706  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
1771        1773  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
3866        3869  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
3864        3867  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
2254        2256  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
1538        1540  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
2142        2144  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   
2379        2381  [(Timestamp('2022-01-01 00:00:01+0000', tz='UT...   

                               stock_out_duration_hours  \
1520  [134.7877777777778, 367.095, 1895.521111111111...   
4267            [1037.9480555555556, 9882.051111111112]   
2704  [2730.528888888889, 13.413055555555555, 8176.0...   
1771             [2685.599722222222, 8234.399444444445]   
3866  [85.25083333333333, 71.26861111111111, 126.019...   
3864  [763.5913888888889, 399.35055555555556, 556.75...   
2254           [451.23583333333335, 10468.763333333334]   
1538  [657.7430555555555, 418.94055555555553, 883.98...   
2142  [1313.8819444444443, 43.63, 149.12277777777777...   
2379  [691.5344444444445, 985.3383333333334, 9243.12...   

                                      stock_out_days  total_stock_out_hours  \
1520                                [5, 15, 78, 355]           10919.999167   
4267                                       [43, 411]           10919.999167   
2704                                   [113, 0, 340]           10919.999167   
1771                                      [111, 343]           10919.999167   
3866   [3, 2, 5, 10, 3, 10, 23, 1, 1, 2, 6, 19, 364]           10919.999167   
3864                           [31, 16, 23, 13, 370]           10919.999167   
2254                                       [18, 436]           10919.999167   
1538                           [27, 17, 36, 18, 355]           10919.999167   
2142  [54, 1, 6, 2, 0, 2, 1, 2, 3, 8, 2, 5, 21, 341]           10919.999167   
2379                                   [28, 41, 385]           10919.999167   

      total_quantity_sold  total_order_ids  
1520                  3.0                3  
4267                  2.0                1  
2704                  2.0                2  
1771                  1.0                1  
3866                 12.0               12  
3864                  4.0                4  
2254                  1.0                1  
1538                  4.0                4  
2142                 13.0               13  
2379                  2.0                2

- From this above two sorted dataframes we can investigate a select number of product ids for the co-occurence analysis. 

    Firstly lets pick the ones which are most sold by order frequency (from the above filteref dataset)

In [66]:
# display the names of top 5 picks from the dataframe sorted_df_123 above
get_product_name(3834,df_product_id_and_name_123)
get_product_name(667,df_product_id_and_name_123)
get_product_name(1279,df_product_id_and_name_123)
get_product_name(3523,df_product_id_and_name_123)
get_product_name(1280,df_product_id_and_name_123)


product_id 3834 product_name Agua Bezoya 1.5L
product_id 667 product_name Agua Font Vella 1.5L
product_id 1279 product_name Agua Solán de Cabras 1.5L
product_id 3523 product_name Hielo Bolsa Cubitos Normales 2kg
product_id 1280 product_name Estrella Damm cerveza lata 33cl


'Estrella Damm cerveza lata 33cl'

- ### Code to identify the number of products occuring with a product

In [5]:

order_product_dict = {}

for _, row in df_sales.iterrows():
    order_id = row['order_id']
    product_id = row['product_id']
    
    if order_id in order_product_dict:
        order_product_dict[order_id].append(product_id)
    else:
        order_product_dict[order_id] = [product_id]

order_product_dict

{'42160': ['742'],
 '17111': ['3834', '779', '475', '4236', '233'],
 '147390': ['3884',
  '1542',
  '703',
  '932',
  '3834',
  '3312',
  '2815',
  '629',
  '1689',
  '4032',
  '362',
  '2035'],
 '31457': ['4144', '1742', '1279', '377', '2350'],
 '6964': ['3771', '1677', '3669', '2668', '4248', '648', '1715'],
 '1340': ['275', '560', '2615', '4074', '2975', '1948', '1312', '528'],
 '105813': ['216',
  '3008',
  '4018',
  '611',
  '3463',
  '880',
  '435',
  '1588',
  '537',
  '1541'],
 '100240': ['751', '433', '752', '3376'],
 '81325': ['3523', '354', '4341'],
 '151103': ['1934', '1948', '528', '1115', '1279', '3165'],
 '97375': ['3391', '3523', '4201'],
 '111873': ['1027', '2804', '610', '528', '3083'],
 '115156': ['147', '2799', '1523', '2301', '2328'],
 '134719': ['1513', '1344', '3445', '353', '697'],
 '30127': ['78', '2444', '1093', '4101', '2348'],
 '143297': ['553', '3602'],
 '95367': ['3676',
  '3445',
  '270',
  '1985',
  '3586',
  '3245',
  '1715',
  '2579',
  '1821',
  '2831

In [6]:
import pandas as pd

# Create a list of unique product IDs
unique_product_ids = df_sales['product_id'].unique().tolist()

# Initialize an empty dictionary to store order IDs for each product ID
order_ids_dict = {}

# Iterate over unique product IDs and store corresponding order IDs in the dictionary
for product_id in unique_product_ids:
    all_order_ids_containing_product = df_sales[df_sales['product_id'] == product_id]['order_id'].tolist()
    order_ids_dict[product_id] = all_order_ids_containing_product

# Initialize an empty list to store co-occurring products
co_occuring_products = []

# Iterate over the order IDs dictionary
for product_id, order_ids in order_ids_dict.items():
    # Filter rows based on the order IDs
    filtered_df = df_sales[df_sales['order_id'].isin(order_ids)]
    # Get unique product IDs in the filtered DataFrame
    unique_co_occuring_products = filtered_df['product_id'].unique().tolist()
    # Remove the current product ID from the list
    unique_co_occuring_products.remove(product_id)
    co_occuring_products.append(unique_co_occuring_products)

# Create a DataFrame with product_id and co_occuring_products columns
co_occuring_df = pd.DataFrame({'product_id': unique_product_ids, 'co_occuring_products': co_occuring_products})


In [7]:
co_occuring_df

product_id                               co_occuring_products
0           742  [752, 4132, 1232, 1779, 3523, 161, 4209, 1610,...
1          3834  [779, 475, 4236, 233, 3884, 1542, 703, 932, 33...
2           779  [3834, 475, 4236, 233, 264, 4164, 1307, 2847, ...
3           475  [3834, 779, 4236, 233, 2362, 2110, 3478, 3648,...
4          4236  [3834, 779, 475, 233, 4060, 766, 40, 1197, 192...
...         ...                                                ...
4358        564  [3533, 1355, 2217, 2336, 3883, 3555, 2320, 236...
4359        350                            [1976, 3640, 3147, 775]
4360       3209                                                 []
4361         97  [3804, 4135, 23, 1544, 3986, 1610, 3040, 674, ...
4362       1602                        [3523, 88, 2221, 912, 2750]

[4363 rows x 2 columns]

In [8]:
# Add a column for the number of co-occurring products
co_occuring_df['number_of_co_occuring_products'] = co_occuring_df['co_occuring_products'].apply(len)

# Sort the DataFrame in descending order by the number of co-occurring products
co_occuring_df = co_occuring_df.sort_values('number_of_co_occuring_products', ascending=False)


---

In [9]:
co_occuring_df

product_id                               co_occuring_products  \
1          3834  [779, 475, 4236, 233, 3884, 1542, 703, 932, 33...   
88          667  [3676, 3445, 270, 1985, 3586, 3245, 1715, 2579...   
19         1279  [4144, 1742, 377, 2350, 1934, 1948, 528, 1115,...   
17         4144  [1742, 1279, 377, 2350, 291, 1755, 2176, 3206,...   
197        1307  [2000, 2047, 2972, 1389, 3709, 2515, 667, 3586...   
...         ...                                                ...   
4139       4348                                                 []   
4323       2207                                                 []   
3974       2162                                                 []   
2510        577                                                 []   
4236       3198                                                 []   

      number_of_co_occuring_products  
1                               3305  
88                              3276  
19                              2965  
17                              2821  
197                             2774  
...                              ...  
4139                               0  
4323                               0  
3974                               0  
2510                               0  
4236                               0  

[4363 rows x 3 columns]

---

# Code to identify the co-occurence of a specefic product id  with all other produts (1 * 4632)

1. We consider a product Xi
2. Then we iterate over the rest of the products one by one,say (Xj), to  generate a pair wise indicator
3. We filter the orders corresponding to which these two products, Xi & Xj,  were in stock
4. Then we create the indiactor as , C_Xi_Xj = [ Number of orders which contain Xi & Xj ] / [Number of orders which contain Xi]

- INPUT FOR THE CO-OCCURENCE FUNCTION :  load the order_level_out_of_stock_df dataframe from csv

In [16]:
import pandas as pd

# Read the CSV file
order_wise_out_of_stock_product_ids = pd.read_csv('order_level_out_of_stock_df.csv')

# Convert the datatype of order_id from int to str
order_wise_out_of_stock_product_ids['order_id'] = order_wise_out_of_stock_product_ids['order_id'].astype(str)

# Display the DataFrame
order_wise_out_of_stock_product_ids.info()

# Display the dataframe
order_wise_out_of_stock_product_ids.head()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 162819 entries, 0 to 162818
Data columns (total 4 columns):
 #   Column                       Non-Null Count   Dtype 
---  ------                       --------------   ----- 
 0   order_id                     162819 non-null  object
 1   order_datetime               162819 non-null  object
 2   out_of_stock_products        162819 non-null  object
 3   products_contained_in_order  162819 non-null  object
dtypes: object(4)
memory usage: 5.0+ MB


order_id             order_datetime  \
0        0  2022-09-12 10:27:01+00:00   
1        1  2022-11-22 17:39:21+00:00   
2       10  2022-02-06 21:15:39+00:00   
3      100  2022-03-11 09:28:00+00:00   
4     1000  2023-01-26 19:54:18+00:00   

                               out_of_stock_products  \
0  ['1', '5', '7', '8', '9', '10', '11', '13', '1...   
1  ['1', '7', '8', '10', '11', '13', '15', '20', ...   
2  ['4', '5', '7', '8', '10', '13', '14', '15', '...   
3  ['4', '5', '7', '8', '10', '13', '15', '18', '...   
4  ['1', '5', '7', '8', '10', '11', '12', '17', '...   

                         products_contained_in_order  
0                                           ['3834']  
1                           ['2495', '4271', '4031']  
2  ['2371', '2445', '3225', '3193', '2529', '3599...  
3  ['2385', '201', '291', '1764', '2156', '688', ...  
4           ['3165', '1344', '2512', '2571', '4317']

- INPUT FOR THE CO-OCCURENCE FUNCTION : product_id_2 will be picked from this List of unique product ids. 

In [17]:
# apparently this is not being used in the function call below

import pandas as pd

# Assuming df_sales is the DataFrame containing the sales data
unique_product_ids = df_sales['product_id'].unique().tolist()

# Convert product IDs to integers
unique_product_ids = [int(pid) for pid in unique_product_ids]

# Sort the list in ascending order
unique_product_ids.sort()

# Convert back to string data type
#unique_product_ids = [str(pid) for pid in unique_product_ids]

# Display the list of unique product IDs
print(unique_product_ids)


[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220, 221,

- DEFINING THE CO-OCCURENCE FUNCTION : All pairs of product_id_1 & product_id_2 will be considered for determining the co-occurence

In [20]:
import pandas as pd

def co_occurrence(product_id_1, product_id_2, order_wise_out_of_stock_product_ids):
    count = 0 

    # Convert product_id_1 to string
    product_id_1 = str(product_id_1)

    # Convert product_id_2 list to strings
    product_id_2 = [str(p) for p in product_id_2]

    # Initialize an empty DataFrame to store the concatenated results
    results_df = pd.DataFrame(columns=['product_id_1', 'product_id_2', 'num_all_orders_with_product_1__when_1_2_are_in_stk', 'num_orders_with_both_product_1_2__when_1_2_are_in_stk', 'co_occurrence_ratio_wrt_product_1'])

    for p2 in product_id_2:

        count = count + 1
        print(count)

        # Create a mask to filter the dataframe for orders for which both products are in stock
        mask = order_wise_out_of_stock_product_ids['out_of_stock_products'].apply(lambda x: (product_id_1 not in x) and (p2 not in x))

        # Apply the mask to obtain the filtered dataframe for orders for which both products are in stock
        filtered_df = order_wise_out_of_stock_product_ids[mask]

        # Count orders with product ID 1 in products_contained_in_order
        orders_with_product_1 = filtered_df[filtered_df['products_contained_in_order'].apply(lambda x: product_id_1 in x)]
        num_orders_with_product_1 = len(orders_with_product_1)

        # Count orders with product ID 1 and product ID 2 in products_contained_in_order
        orders_with_product_1_2 = filtered_df[filtered_df['products_contained_in_order'].apply(lambda x: product_id_1 in x and p2 in x)]
        num_orders_with_product_1_2 = len(orders_with_product_1_2)

        # Calculate co-occurrence ratio
        if num_orders_with_product_1 > 0:
            co_occurrence_ratio = num_orders_with_product_1_2 / num_orders_with_product_1
        else:
            co_occurrence_ratio = np.nan

        # Append the results to the DataFrame
        results_df = results_df.append({'product_id_1': product_id_1,
                                        'product_id_2': p2,
                                        'num_all_orders_with_product_1__when_1_2_are_in_stk': num_orders_with_product_1,
                                        'num_orders_with_both_product_1_2__when_1_2_are_in_stk': num_orders_with_product_1_2,
                                        'co_occurrence_ratio_wrt_product_1': co_occurrence_ratio},
                                       ignore_index=True)
        
        # Sort by ratio
        results_df = results_df.sort_values('co_occurrence_ratio_wrt_product_1', ascending=False).reset_index(drop=True)

        '''
        # Append the results to the DataFrame
        results_df = results_df.append({'product_id_1': product_id_1,
                                        'product_id_2': p2,
                                        'num_all_orders_with_product_1__when_1_2_are_in_stk': num_orders_with_product_1,
                                        'num_orders_with_both_product_1_2__when_1_2_are_in_stk': num_orders_with_product_1_2},
                                       ignore_index=True)
        '''

    return results_df


- FUNCTION CALL WITH DIFFERENT CHOICES OF product_id_1.

    product_id_1 is chosen from the list of the problematic products, those having high frequency of orders and also having stock outs

### (i)  first run to determine co-occurence indicator for product_id_1 : 3834

In [21]:
get_product_name(3834,df_product_id_and_name_123)

product_id 3834 product_name Agua Bezoya 1.5L


'Agua Bezoya 1.5L'

In [22]:
# defining the input for the functino call
product_id_1 = 3834
product_id_2 = unique_product_ids 

# the function call
result_df = co_occurrence(product_id_1, product_id_2, order_wise_out_of_stock_product_ids)

# Create the csv file with the product_id_1 in the filename
csv_filename = f"final_co_occurrence_ratio_for_{product_id_1}.csv"
result_df.to_csv(csv_filename, index=False, mode='w')

# display the output
result_df


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


product_id_1 product_id_2  \
0            3834         3834   
1            3834          610   
2            3834         1610   
3            3834         2668   
4            3834          752   
...           ...          ...   
4358         3834         4179   
4359         3834         4241   
4360         3834         4246   
4361         3834         4270   
4362         3834         4278   

     num_all_orders_with_product_1__when_1_2_are_in_stk  \
0                                                 14741   
1                                                  2073   
2                                                  4758   
3                                                  7865   
4                                                    15   
...                                                 ...   
4358                                                  0   
4359                                                  0   
4360                                                  0   
4361                                                  0   
4362                                                  0   

     num_orders_with_both_product_1_2__when_1_2_are_in_stk  \
0                                                 14741      
1                                                   142      
2                                                   325      
3                                                   526      
4                                                     1      
...                                                 ...      
4358                                                  0      
4359                                                  0      
4360                                                  0      
4361                                                  0      
4362                                                  0      

      co_occurrence_ratio_wrt_product_1  
0                              1.000000  
1                              0.068500  
2                              0.068306  
3                              0.066879  
4                              0.066667  
...                                 ...  
4358                                NaN  
4359                                NaN  
4360                                NaN  
4361                                NaN  
4362                                NaN  

[4363 rows x 5 columns]

### (ii)  second run to determine co-occurence indicator for product_id_1 : 667

In [194]:
get_product_name(667,df_product_id_and_name_123)

product_id 667 product_name Agua Font Vella 1.5L


'Agua Font Vella 1.5L'

In [23]:
# defining the input for the functino call
product_id_1 = 667
product_id_2 = unique_product_ids 

# the function call
result_df = co_occurrence(product_id_1, product_id_2, order_wise_out_of_stock_product_ids)

# Create the csv file with the product_id_1 in the filename
csv_filename = f"final_co_occurrence_ratio_for_{product_id_1}.csv"
result_df.to_csv(csv_filename, index=False, mode='w')

# display the output
result_df


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


product_id_1 product_id_2  \
0             667          667   
1             667         2668   
2             667         3667   
3             667         3016   
4             667         4091   
...           ...          ...   
4358          667         4344   
4359          667         4345   
4360          667         4348   
4361          667         4353   
4362          667         4355   

     num_all_orders_with_product_1__when_1_2_are_in_stk  \
0                                                    26   
1                                                    26   
2                                                    26   
3                                                    19   
4                                                    26   
...                                                 ...   
4358                                                  0   
4359                                                  0   
4360                                                  0   
4361                                                  0   
4362                                                  0   

     num_orders_with_both_product_1_2__when_1_2_are_in_stk  \
0                                                    26      
1                                                     4      
2                                                     3      
3                                                     2      
4                                                     2      
...                                                 ...      
4358                                                  0      
4359                                                  0      
4360                                                  0      
4361                                                  0      
4362                                                  0      

      co_occurrence_ratio_wrt_product_1  
0                              1.000000  
1                              0.153846  
2                              0.115385  
3                              0.105263  
4                              0.076923  
...                                 ...  
4358                                NaN  
4359                                NaN  
4360                                NaN  
4361                                NaN  
4362                                NaN  

[4363 rows x 5 columns]

### (iii)  third run to determine co-occurence indicator for product_id_1 : 3523

In [188]:
get_product_name(3523,df_product_id_and_name_123)

product_id 3523 product_name Hielo Bolsa Cubitos Normales 2kg


'Hielo Bolsa Cubitos Normales 2kg'

In [199]:
# defining the input for the functino call
product_id_1 = 3523
product_id_2 = unique_product_ids
out_of_stock_products = filtered_df  # Use your actual dataframe here

# the function call
result_df = co_occurrence(product_id_1, product_id_2, out_of_stock_products)

# Create the csv file with the product_id_1 in the filename
csv_filename = f"final_co_occurrence_ratio_for_{product_id_1}.csv"
result_df.to_csv(csv_filename, index=False, mode='w')

# display the output
result_df


product_id_1 product_id_2 num_orders_with_product_1  \
0            3523         3523                         5   
1            3523         3834                         5   
2            3523         1669                         5   
3            3523         1384                         5   
4            3523          873                         5   
...           ...          ...                       ...   
4358         3523         4278                         0   
4359         3523          564                         0   
4360         3523          350                         0   
4361         3523           97                         0   
4362         3523         1602                         0   

     num_orders_with_product_1_2  co_occurrence_ratio  
0                              5                  1.0  
1                              2                  0.4  
2                              1                  0.2  
3                              1                  0.2  
4                              1                  0.2  
...                          ...                  ...  
4358                           0                  NaN  
4359                           0                  NaN  
4360                           0                  NaN  
4361                           0                  NaN  
4362                           0                  NaN  

[4363 rows x 5 columns]

### (iv)  fourth run to determine co-occurence indicator for product_id_1 : 1280

In [189]:
get_product_name(1280,df_product_id_and_name_123)

product_id 1280 product_name Estrella Damm cerveza lata 33cl


'Estrella Damm cerveza lata 33cl'

In [200]:
# defining the input for the functino call
product_id_1 = 1280
product_id_2 = unique_product_ids
out_of_stock_products = filtered_df  # Use your actual dataframe here

# the function call
result_df = co_occurrence(product_id_1, product_id_2, out_of_stock_products)

# Create the csv file with the product_id_1 in the filename
csv_filename = f"final_co_occurrence_ratio_for_{product_id_1}.csv"
result_df.to_csv(csv_filename, index=False, mode='w')

# display the output
result_df


product_id_1 product_id_2 num_orders_with_product_1  \
0            1280         3911                         7   
1            1280         1280                         8   
2            1280         4132                         8   
3            1280         1506                         8   
4            1280         3728                         8   
...           ...          ...                       ...   
4358         1280         4278                         0   
4359         1280          564                         0   
4360         1280          350                         0   
4361         1280           97                         0   
4362         1280         1602                         0   

     num_orders_with_product_1_2  co_occurrence_ratio  
0                              7                1.000  
1                              8                1.000  
2                              1                0.125  
3                              1                0.125  
4                              1                0.125  
...                          ...                  ...  
4358                           0                  NaN  
4359                           0                  NaN  
4360                           0                  NaN  
4361                           0                  NaN  
4362                           0                  NaN  

[4363 rows x 5 columns]

---

---